In [1]:
import pandas as pd
import folium
import math

In [2]:
# list of dates for the downloaded files
# '201901','201902','201903','201904','201905','201906','201907','201908','201909','201910','201911','201912',
#             '202001','202002','202003','202004','202005','202006','202007','202008','202009','202010','202011','202012',
#             '202101','202102','202103','202104','202105','202106', '202107','202108','202109'
lstDates = ['202106',
            '202107',
            '202107'
           ]

In [3]:
lstdf = []
# a loop to read the monthly csv files 
for date in lstDates:
    try:
        # read each month's csv
        pathname = r"D:\Dropbox\Teaching\AGIS_Spring_2022\Data\citi_bikes\{}-citibike-tripdata.csv\{}-citibike-tripdata.csv".format(date,date)
        # add (append) this to a list
        lstdf.append(pd.read_csv(pathname))
    except:
        print('got an error for ',date)

C:\Users\mp5160\Anaconda3\envs\AGIS\lib\site-packages\IPython\core\interactiveshell.py:3251: DtypeWarning: Columns (7) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)


In [4]:
# put together all monthly dataframe and create one big dataframe
dfall = pd.concat(lstdf)

In [5]:
len(dfall)

9346591

In [7]:
dfall.sample(2)

ride_id rideable_type           started_at  \
1391072  3B02AA56750F8B7D  classic_bike  2021-07-27 19:38:12   
1331651  41F7B4272B1F76D8  classic_bike  2021-07-30 19:00:52   

                    ended_at    start_station_name  start_station_id  \
1391072  2021-07-27 19:59:02  West St & Liberty St           5184.08   
1331651  2021-07-30 19:18:08       E 25 St & 2 Ave           6046.02   

        end_station_name end_station_id  start_lat  start_lng    end_lat  \
1391072  8 Ave & W 31 St        6450.05  40.711444 -74.014847  40.750585   
1331651  E 84 St & 1 Ave        7180.02  40.739126 -73.979738  40.775655   

           end_lng member_casual  
1391072 -73.994685        member  
1331651 -73.950686        member

In [8]:
# convert the columns to datetime object
dfall['started_at'] = pd.to_datetime(dfall['started_at'],format='%Y-%m-%d')
dfall['ended_at'] = pd.to_datetime(dfall['ended_at'],format='%Y-%m-%d')
# calculate duration of each trip
dfall['tripduration'] = dfall['ended_at']-dfall['started_at']


In [67]:
dfall['started_hour'] = (dfall['started_at'].dt.hour % 24 + 4) // 4
dfall['started_hour'].replace({1: 'Late Night',
                      2: 'Early Morning',
                      3: 'Morning',
                      4: 'Noon',
                      5: 'Evening',
                      6: 'Night'}, inplace=True)

In [68]:
dfall['started_hour'].unique()

array(['Evening', 'Night', 'Morning', 'Noon', 'Early Morning',
       'Late Night'], dtype=object)

In [41]:
dfall['member_casual'].unique()

array(['member', 'casual'], dtype=object)

In [40]:
dfall['rideable_type'].unique()

array(['docked_bike', 'classic_bike'], dtype=object)

In [19]:
dfall['start_station_id'] = pd.to_numeric(dfall['start_station_id'], errors='coerce')
dfall = dfall.loc[~dfall['start_station_id'].isna()]
dfall['end_station_id'] = pd.to_numeric(dfall['end_station_id'], errors='coerce')
dfall = dfall.loc[~dfall['end_station_id'].isna()]

### Mapping stations

In [20]:
# create a dataframe that is consolidated based on start station; get the first lat and long value (all lat and long values should be the same)
dfStarts = (dfall[['start_station_id','start_lat','start_lng']]).groupby(['start_station_id']).agg({'start_lat':['first'],'start_lng':['first']})
# create a dataframe that is consolidated based on end station; get the first lat and long value (all lat and long values should be the same)
dfEnds = (dfall[['end_station_id','end_lat','end_lng']]).groupby(['end_station_id']).agg({'end_lat':['first'],'end_lng':['first']})

In [21]:
# fix the levels
dfStarts = dfStarts.droplevel(1,axis=1).reset_index()
dfEnds = dfEnds.droplevel(1,axis=1).reset_index()

In [22]:
# rename the columns to make them consistent
dfEnds = dfEnds.rename(columns={'end_station_id': 'station_id', 'end_lat': 'latitude','end_lng': 'longitude'})
dfStarts = dfStarts.rename(columns={'start_station_id': 'station_id', 'start_lat': 'latitude','start_lng': 'longitude'})

In [23]:
dfStations = pd.concat([dfStarts,dfEnds])
# convert station_id to a numeric variable



In [24]:
dfStations.sample(2)

station_id   latitude  longitude
370      4895.03  40.702461 -73.986842
1067     7622.12  40.800672 -73.934900

In [25]:
dfStations.info()

<class 'pandas.core.frame.DataFrame'>
Int64Index: 2984 entries, 0 to 1492
Data columns (total 3 columns):
 #   Column      Non-Null Count  Dtype  
---  ------      --------------  -----  
 0   station_id  2984 non-null   float64
 1   latitude    2984 non-null   float64
 2   longitude   2984 non-null   float64
dtypes: float64(3)
memory usage: 93.2 KB


In [26]:
dfStations.drop_duplicates(subset=None, keep="first", inplace=True)

In [27]:
print ('the total number of stations is: ', len(dfStations))

the total number of stations is:  1971


In [28]:
dfStations.to_csv(r'D:\Dropbox\Teaching\AGIS_Spring_2022\Data\citi_bikes\citiBikeStations.csv')

In [29]:
# create a list of points
locations = dfStations[['latitude', 'longitude','station_id']]
locationlist = locations.values.tolist()
len(locationlist)

1971

In [30]:
# use Folium to map the points
map = folium.Map(location=[dfStations['latitude'].mean(), dfStations['longitude'].mean()], zoom_start=12)
for point in locationlist:
    folium.Circle(
        radius=5,                                                     # the size of circles
        location=point[0:2],                                          # lat and long of the points
        popup='Id: {}'.format(point[2]), # the popup message
        color="black",                                                # color of the circle
        fill=True,
    ).add_to(map)
map

### Station connections

In [88]:
# choose the id of a station
thisStation = 3208.07
# choose the bike type
# ['docked_bike', 'classic_bike']
bikeType = ['docked_bike', 'classic_bike']
# choose member type
#  ['member', 'casual']
memberType = ['member', 'casual']
# choose the startHour
# ['Evening', 'Night', 'Morning', 'Noon', 'Early Morning', 'Late Night']
tripHour = ['Evening', 'Night', 'Morning', 'Noon', 'Early Morning', 'Late Night']

In [89]:
# get the lat and long of the station
thisCoors = (dfStations.loc[(dfStations['station_id']==thisStation)])[['latitude','longitude']]
thisCoors =thisCoors.values.tolist()[0]
thisCoors

[40.646037, -73.980963]

In [90]:
# filter the big table to separate all trips from one start station
dfThis = dfall.loc[(dfall['start_station_id']==thisStation)&
                   (dfall['rideable_type'].isin(bikeType))&
                   (dfall['member_casual'].isin(memberType))&
                   (dfall['started_hour'].isin(tripHour))
                  ]
dfThis.sample(2)

ride_id rideable_type          started_at  \
2209311  D553EAAB021E4F23  classic_bike 2021-07-01 21:28:23   
1205711  D80273E12C4D79D9  classic_bike 2021-07-20 23:13:23   

                   ended_at  start_station_name  start_station_id  \
2209311 2021-07-01 21:43:22  Dahill Rd & 12 Ave           3208.07   
1205711 2021-07-20 23:39:45  Dahill Rd & 12 Ave           3208.07   

             end_station_name  end_station_id  start_lat  start_lng  \
2209311    Dahill Rd & 12 Ave         3208.07  40.646037 -73.980963   
1205711  Chester Ave & 12 Ave         3135.04  40.646037 -73.980963   

           end_lat    end_lng member_casual    tripduration started_hour  
2209311  40.646037 -73.980963        member 0 days 00:14:59        Night  
1205711  40.644367 -73.984276        member 0 days 00:26:22        Night

In [91]:
len(dfThis)

1152

In [92]:
# groupby the filtered dataframe based on the station id of the destinations (carry some variables such as number of trips, average of duration)
dfThisDest = dfThis.groupby(['end_station_id']).agg({'tripduration':['count','mean']})
dfThisDest = dfThisDest.droplevel(0,axis=1).reset_index()
dfThisDest = dfThisDest.rename(columns={'end_station_id': 'station_id', 'mean': 'tripDurationMean'})
dfThisDest.sample(2)

station_id  count          tripDurationMean
7      3056.05     35 0 days 00:16:22.571428571
50     3611.02      5    0 days 00:14:03.600000

In [93]:
print('the number of destinations from station id: {} is: '.format(thisStation),len(dfThisDest))

the number of destinations from station id: 3208.07 is:  170


In [94]:
# if we merge/join this with the station tables that has coordinates, then we have locations!

dfThisMergedDest = pd.merge(dfStations,dfThisDest,on='station_id',how='inner')
dfThisMergedDest.sample(2)


station_id   latitude  longitude  count       tripDurationMean
62      3722.04  40.665146 -73.976376      8 0 days 00:22:33.625000
212     5453.01  40.721101 -73.991925      1        0 days 00:41:14

In [111]:
# now let's map them!

locations = dfThisMergedDest[['latitude', 'longitude','station_id','count','tripDurationMean']]
locationlist = locations.values.tolist()

map2 = folium.Map(location=[dfThisMergedDest['latitude'].mean(), dfThisMergedDest['longitude'].mean()], zoom_start=12)

for point in locationlist:
    folium.Circle(
        radius=math.sqrt(point[3])*15,
        location=point[0:2],
        popup='Id: {}; trip counts: {}; averageDuration {}'.format(point[2],point[3],point[4]),
        color="blue",
        fill=True,
    ).add_to(map2)
    
    
# the location of origin station  
folium.Circle(
        radius=30,
        location=thisCoors,
        popup='your stations',
        color="red",
        fill=True,
    ).add_to(map2)
    
map2

### Let's create a fetch function!

In [108]:

def fetchStation(thisStation,bikeType,memberType,tripHour):
    # get the lat and long of the station
    thisCoors = (dfStations.loc[(dfStations['station_id']==thisStation)])[['latitude','longitude']]
    thisCoors =thisCoors.values.tolist()[0]
    # filter the big table to separate all trips from one start station
    dfThis = dfall.loc[(dfall['start_station_id']==thisStation)&
                   (dfall['rideable_type'].isin(bikeType))&
                   (dfall['member_casual'].isin(memberType))&
                   (dfall['started_hour'].isin(tripHour))
                  ]
    # groupby the filtered dataframe based on the station id of the destinations (carry some variables such as number of trips, average of duration)
    dfThisDest = dfThis.groupby(['end_station_id']).agg({'tripduration':['count','mean']})
    dfThisDest = dfThisDest.droplevel(0,axis=1).reset_index()
    dfThisDest = dfThisDest.rename(columns={'end_station_id': 'station_id', 'mean': 'tripDurationMean'})
    dfThisMergedDest = pd.merge(dfStations,dfThisDest,on='station_id',how='inner')
    locations = dfThisMergedDest[['latitude', 'longitude','station_id','count','tripDurationMean']]
    locationlist = locations.values.tolist()

    map2 = folium.Map(location=[dfThisMergedDest['latitude'].mean(), dfThisMergedDest['longitude'].mean()], zoom_start=12)

    for point in locationlist:
        folium.Circle(
            radius=math.sqrt(point[3])*15,
            location=point[0:2],
            popup='Id: {}; trip counts: {}; averageDuration {}'.format(point[2],point[3],point[4]),
            color="blue",
            fill=True,
        ).add_to(map2)


    # the location of origin station  
    folium.Circle(
            radius=50,
            location=thisCoors,
            popup='your stations',
            color="red",
            fill=True,
        ).add_to(map2)
    
    return map2


In [109]:
# choose the id of a station
thisStation = 3376.02
# choose the bike type
# ['docked_bike', 'classic_bike']
bikeType = ['docked_bike', 'classic_bike']
# choose member type
#  ['member', 'casual']
memberType = ['member', 'casual']
# choose the startHour
# ['Early Morning','Morning','Noon','Evening', 'Night', 'Late Night']
tripHour = ['Early Morning','Morning','Noon','Evening', 'Night', 'Late Night']

In [110]:
fetchStation(thisStation,bikeType,memberType,tripHour)